In [2]:
import pandas as pd
import numpy as np
import re
import pickle
import nltk
from nltk.corpus import stopwords

from numpy import array
from keras.preprocessing.text import one_hot
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers.core import Activation, Dropout, Dense
from keras.layers import Flatten, LSTM, Bidirectional, Conv1D, GRU
from keras.layers import GlobalMaxPooling1D, GlobalAveragePooling1D
from keras.layers.embeddings import Embedding
from sklearn.model_selection import train_test_split
from keras.preprocessing.text import Tokenizer
#from sklearn.preprocessing import LabelBinarizer
from sklearn.preprocessing import LabelEncoder
from imblearn.over_sampling import RandomOverSampler
from collections import Counter

Using TensorFlow backend.
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
C:\ProgramData\Anaconda3\lib\site-packages\tensorflow\python\framework\dtypes.py

In [3]:
dataset = pd.read_csv("dataset.csv")
#dataset.dropna(inplace=True)

dataset

review sentiment
0      One of the other reviewers has mentioned that ...  positive
1      A wonderful little production. <br /><br />The...  positive
2      I thought this was a wonderful way to spend ti...  positive
3      Basically there's a family where a little boy ...  negative
4      Petter Mattei's "Love in the Time of Money" is...  positive
...                                                  ...       ...
49975  I thought this movie did a down right good job...  positive
49976  Bad plot, bad dialogue, bad acting, idiotic di...  negative
49977  I am a Catholic taught in parochial elementary...  negative
49978  I'm going to have to disagree with the previou...  negative
49979  No one expects the Star Trek movies to be high...  negative

[49980 rows x 2 columns]

In [4]:
#dataset.drop('Unnamed: 0',axis="columns",inplace=True)


In [5]:
dataset

review sentiment
0      One of the other reviewers has mentioned that ...  positive
1      A wonderful little production. <br /><br />The...  positive
2      I thought this was a wonderful way to spend ti...  positive
3      Basically there's a family where a little boy ...  negative
4      Petter Mattei's "Love in the Time of Money" is...  positive
...                                                  ...       ...
49975  I thought this movie did a down right good job...  positive
49976  Bad plot, bad dialogue, bad acting, idiotic di...  negative
49977  I am a Catholic taught in parochial elementary...  negative
49978  I'm going to have to disagree with the previou...  negative
49979  No one expects the Star Trek movies to be high...  negative

[49980 rows x 2 columns]

In [6]:
dataset['sentiment'].unique()

array(['positive', 'negative'], dtype=object)

In [7]:
dataset['sentiment'].nunique()

2

In [8]:
def preprocess_text(sen):
    sentence = remove_tags(sen)
    sentence = re.sub('[^a-zA-Z]', ' ', sentence)
    sentence = re.sub(r"\s+[a-zA-Z]\s+", ' ', sentence)
    sentence = re.sub(r'\s+', ' ', sentence)
    return sentence

In [9]:
TAG_RE = re.compile(r'<[^>]+>')
def remove_tags(text):
    return TAG_RE.sub('', text)

In [10]:
X = []
sentences = list(dataset['review'])
for sen in sentences:
    X.append(preprocess_text(sen))
X=pd.DataFrame({'review':X})
X

review
0      One of the other reviewers has mentioned that ...
1      A wonderful little production The filming tech...
2      I thought this was wonderful way to spend time...
3      Basically there a family where little boy Jake...
4      Petter Mattei Love in the Time of Money is vis...
...                                                  ...
49975  I thought this movie did down right good job I...
49976  Bad plot bad dialogue bad acting idiotic direc...
49977  I am Catholic taught in parochial elementary s...
49978  I going to have to disagree with the previous ...
49979  No one expects the Star Trek movies to be high...

[49980 rows x 1 columns]

In [11]:
y=dataset['sentiment']
y

0        positive
1        positive
2        positive
3        negative
4        positive
           ...   
49975    positive
49976    negative
49977    negative
49978    negative
49979    negative
Name: sentiment, Length: 49980, dtype: object

In [12]:
le=LabelEncoder()
le.fit(y)
y=le.transform(y)
y

array([1, 1, 1, ..., 0, 0, 0])

In [13]:
print('Original dataset shape %s' % Counter(y))

Original dataset shape Counter({1: 24993, 0: 24987})


In [14]:
ros = RandomOverSampler(random_state=42)
x_res, y_res = ros.fit_resample(X,y)
x_res

review
0      One of the other reviewers has mentioned that ...
1      A wonderful little production The filming tech...
2      I thought this was wonderful way to spend time...
3      Basically there a family where little boy Jake...
4      Petter Mattei Love in the Time of Money is vis...
...                                                  ...
49981  This movie had the potential to be far more th...
49982  Obviously the comments above that fawn over th...
49983  The plot outline of this movie is similar to t...
49984  Entrails of Virgin is so bizarre and incompreh...
49985  This movie really is that bad and m normally s...

[49986 rows x 1 columns]

In [15]:
y_res

array([1, 1, 1, ..., 0, 0, 0])

In [16]:
print('Resampled dataset shape %s' % Counter(y_res))

Resampled dataset shape Counter({1: 24993, 0: 24993})


In [17]:
x_res=x_res['review']
x_res

0        One of the other reviewers has mentioned that ...
1        A wonderful little production The filming tech...
2        I thought this was wonderful way to spend time...
3        Basically there a family where little boy Jake...
4        Petter Mattei Love in the Time of Money is vis...
                               ...                        
49981    This movie had the potential to be far more th...
49982    Obviously the comments above that fawn over th...
49983    The plot outline of this movie is similar to t...
49984    Entrails of Virgin is so bizarre and incompreh...
49985    This movie really is that bad and m normally s...
Name: review, Length: 49986, dtype: object

In [18]:
X_train, X_test, y_train, y_test = train_test_split(x_res, y_res, test_size=0.20, random_state=42)

In [19]:
tokenizer = Tokenizer(num_words=10000)
tokenizer.fit_on_texts(x_res)

In [20]:
X_train = tokenizer.texts_to_sequences(X_train)
X_test = tokenizer.texts_to_sequences(X_test)

In [21]:
X_train

[[24,
  3,
  1,
  114,
  94,
  119,
  1,
  317,
  3,
  1398,
  2889,
  2137,
  66,
  26,
  56,
  25,
  5275,
  8358,
  36,
  30,
  2791,
  52,
  782,
  7,
  54,
  647,
  15,
  271,
  383,
  1,
  884,
  829,
  1593,
  4431,
  1,
  186,
  252,
  736,
  295,
  5275,
  11,
  6,
  139,
  25,
  217,
  271,
  19,
  815,
  1913,
  4327,
  2,
  22,
  76,
  8511,
  6161,
  894,
  9,
  13,
  385,
  46,
  383,
  253,
  508,
  1772,
  829,
  33,
  1,
  446,
  4,
  1,
  875,
  2,
  253,
  2531,
  524,
  55,
  47,
  1,
  12,
  5,
  117,
  41,
  17,
  129,
  152,
  99,
  6,
  138,
  201,
  144,
  2,
  172,
  172],
 [124,
  84,
  207,
  8,
  16,
  7,
  7,
  1,
  12,
  1461,
  96,
  103,
  3602,
  4708,
  2,
  4184,
  3,
  1,
  366,
  6,
  129,
  162,
  64,
  416,
  39,
  1305,
  412,
  6,
  127,
  3,
  157,
  582,
  5330,
  198,
  262,
  7,
  636,
  690,
  824,
  15,
  65,
  2139,
  5,
  65,
  2139,
  15,
  6,
  78,
  6696,
  3,
  87,
  582,
  5939,
  3,
  1107,
  293,
  9276,
  1,
  919,
  4738,
  2,


In [22]:
X_test

[[124,
  23,
  287,
  8,
  12,
  272,
  206,
  1,
  233,
  53,
  789,
  8376,
  182,
  1422,
  133,
  4,
  164,
  3539,
  13,
  1,
  108,
  379,
  1,
  108,
  5,
  19,
  1347,
  4,
  2897,
  292,
  36,
  379,
  131,
  2484,
  3233,
  21,
  7,
  1,
  108,
  80,
  2000,
  2164,
  3,
  3435,
  691,
  5,
  245,
  185,
  1,
  184,
  2000,
  2419,
  3509,
  5412,
  126,
  5,
  184,
  242,
  31,
  42,
  6352,
  30,
  1092,
  14,
  1,
  3,
  961,
  223,
  50,
  200,
  23,
  63,
  339,
  4,
  4068,
  8,
  49,
  3353,
  4097,
  15,
  107,
  183,
  4,
  23,
  95,
  223,
  4343,
  27,
  26,
  50,
  107,
  183,
  4,
  23,
  95,
  4675,
  50,
  46,
  465,
  4,
  47,
  1,
  3122,
  3,
  24,
  3,
  38,
  6166,
  3944,
  185,
  896,
  2000,
  5335,
  30,
  2165,
  3,
  1612,
  14,
  38,
  76,
  106,
  2273,
  2294,
  2303,
  89,
  47,
  2273,
  96,
  1,
  1588,
  321,
  3,
  38,
  575,
  1711,
  2000,
  1089,
  673,
  83,
  6126,
  2,
  5,
  5460,
  14,
  38,
  196,
  1889,
  200,
  23,
  1026,
  136,


In [23]:
vocab_size = len(tokenizer.word_index) + 1
maxlen = 100
vocab_size

101389

In [24]:
X_train = pad_sequences(X_train, padding='post', maxlen=maxlen)
X_test = pad_sequences(X_test, padding='post', maxlen=maxlen)

In [25]:
X_train

array([[  24,    3,    1, ...,    0,    0,    0],
       [   8,   16,    7, ...,  116,  106,    6],
       [  29, 9432,  873, ...,   23,    1, 1412],
       ...,
       [ 780,    8,   24, ...,    0,    0,    0],
       [   8,  347,   10, ...,    0,    0,    0],
       [ 100,  121,   76, ...,   67,   69, 1965]])

In [26]:
X_test

array([[   1,  316, 2000, ...,    7,   54, 2004],
       [  98,    8,   59, ...,  609,  652,   59],
       [1681, 1265,   10, ...,  113,   19,  158],
       ...,
       [  63, 4672,  105, ...,  161,  417,   65],
       [  52,  452,    2, ..., 7404,    1, 2353],
       [  88,   80,   28, ...,    3,    1,   53]])

In [27]:
X_train.shape

(39988, 100)

In [28]:
y_train.shape

(39988,)

In [29]:
embeddings_dictionary = dict()
with open('glove.6B.100d.txt', encoding="utf8") as glove_file:
    for line in glove_file:
        records = line.split()
        word = records[0]
        vector_dimensions = np.asarray(records[1:], dtype='float32')
        embeddings_dictionary [word] = vector_dimensions
        
embedding_matrix = np.zeros((vocab_size, 100))
for word, index in tokenizer.word_index.items():
    embedding_vector = embeddings_dictionary.get(word)
    if embedding_vector is not None:
        embedding_matrix[index] = embedding_vector

In [30]:
model = Sequential([
    Embedding(vocab_size, 100, weights=[embedding_matrix], input_length=maxlen , trainable=False),
    Bidirectional(LSTM(50, dropout=0.2, recurrent_dropout=0.2, return_sequences=True)),
    Bidirectional(LSTM(54, dropout=0.3, recurrent_dropout=0.3, return_sequences=True)),
    Bidirectional(LSTM(60, dropout=0.3, recurrent_dropout=0.3)),
    Dense(64, activation="relu"),
    Dense(2, activation="softmax")])

model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])
model.summary()

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (None, 100, 100)          10138900  
_________________________________________________________________
bidirectional_1 (Bidirection (None, 100, 100)          60400     
_________________________________________________________________
bidirectional_2 (Bidirection (None, 100, 108)          66960     
_________________________________________________________________
bidirectional_3 (Bidirection (None, 120)               81120     
_________________________________________________________________
dense_1 (Dense)              (None, 64)                7744      
_________________________________________________________________
dense_2 (Dense)      

In [31]:
history = model.fit(X_train, y_train, batch_size=128, epochs=5, verbose=1, validation_split=0.2)

Instructions for updating:
Use tf.cast instead.
Train on 31990 samples, validate on 7998 samples
Epoch 1/5
31990/31990 [==============================] - 310s 10ms/step - loss: 0.6042 - acc: 0.6651 - val_loss: 0.4772 - val_acc: 0.7754
Epoch 2/5
31990/31990 [==============================] - 356s 11ms/step - loss: 0.4950 - acc: 0.7650 - val_loss: 0.4254 - val_acc: 0.8033
Epoch 3/5
31990/31990 [==============================] - 381s 12ms/step - loss: 0.4506 - acc: 0.7895 - val_loss: 0.4037 - val_acc: 0.8127
Epoch 4/5
31990/31990 [==============================] - 331s 10ms/step - loss: 0.4239 - acc: 0.8059 - val_loss: 0.3793 - val_acc: 0.8278
Epoch 5/5
31990/31990 [==============================] - 325s 10ms/step - loss: 0.4057 - acc: 0.8135 - val_loss: 0.3663 - val_acc: 0.8375


In [32]:
"""model.save("model_final.model")
np.save("class_names.npy", encoder.classes_)"""
with open('label.pickle', 'wb') as handle:
    pickle.dump(le, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [33]:
with open('tokenizer.pickle', 'wb') as handle:
    pickle.dump(tokenizer, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [34]:
import matplotlib.pyplot as plt

plt.figure(1, figsize = (15,8)) 
    
plt.subplot(221)  
plt.plot(history.history['acc'])  
plt.plot(history.history['val_acc'])  
plt.title('model accuracy')  
plt.ylabel('accuracy')  
plt.xlabel('epoch')  
plt.legend(['train', 'valid']) 
    
plt.subplot(222)  
plt.plot(history.history['loss'])  
plt.plot(history.history['val_loss'])  
plt.title('model loss')  
plt.ylabel('loss')  
plt.xlabel('epoch')  
plt.legend(['train', 'valid']) 

plt.show()

<Figure size 1500x800 with 2 Axes>

In [35]:
model.save("model_final.hdf5")